In [1]:
import os
os.environ["VLLM_USE_V1"] = '0'

Add the above line to not causing a vllm error

In [ ]:
from unsloth import FastLanguageModel, is_bfloat16_supported
import torch
max_seq_length = 1024
lora_rank = 64

model, tokenizer = FastLanguageModel.from_pretrained(
    model_name = "Qwen/Qwen2.5-3B-Instruct",
    max_seq_length = max_seq_length,
    load_in_4bit = True, 
    fast_inference = True, 
    max_lora_rank = lora_rank,
    gpu_memory_utilization = 0.5, 
)

model = FastLanguageModel.get_peft_model(
    model,
    r = lora_rank,
    target_modules = [
        "q_proj", "k_proj", "v_proj", "o_proj",
        "gate_proj", "up_proj", "down_proj",
    ],
    lora_alpha = lora_rank,
    use_gradient_checkpointing = "unsloth",
    random_state = 2811,
)

🦥 Unsloth: Will patch your computer to enable 2x faster free finetuning.
Unsloth: Failed to patch SmolVLMForConditionalGeneration forward function.
🦥 Unsloth Zoo will now patch everything to make training faster!
INFO 04-30 22:50:01 [__init__.py:239] Automatically detected platform cuda.
==((====))==  Unsloth 2025.4.1: Fast Qwen2 patching. Transformers: 4.51.3. vLLM: 0.8.4.
   \\   /|    NVIDIA GeForce RTX 4070 Ti SUPER. Num GPUs = 1. Max memory: 15.992 GB. Platform: Linux.
O^O/ \_/ \    Torch: 2.6.0+cu124. CUDA: 8.9. CUDA Toolkit: 12.4. Triton: 3.2.0
\        /    Bfloat16 = TRUE. FA [Xformers = 0.0.29.post2. FA2 = False]
 "-____-"     Free license: http://github.com/unslothai/unsloth
Unsloth: Fast downloading is enabled - ignore downloading bars which are red colored!
Unsloth: vLLM loading unsloth/qwen2.5-3b-instruct-unsloth-bnb-4bit with actual GPU utilization = 45.97%
Unsloth: Your GPU has CUDA compute capability 8.9 with VRAM = 15.99 GB.
Unsloth: Using conservativeness = 1.0. Chun

Loading safetensors checkpoint shards:   0% Completed | 0/1 [00:00<?, ?it/s]


Loading safetensors checkpoint shards:   0% Completed | 0/1 [00:00<?, ?it/s]


INFO 04-30 22:50:20 [punica_selector.py:18] Using PunicaWrapperGPU.
INFO 04-30 22:50:20 [model_runner.py:1146] Model loading took 2.4392 GiB and 3.879250 seconds
INFO 04-30 22:50:21 [worker.py:267] Memory profiling takes 0.88 seconds
INFO 04-30 22:50:21 [worker.py:267] the current vLLM instance can use total_gpu_memory (15.99GiB) x gpu_memory_utilization (0.46) = 7.35GiB
INFO 04-30 22:50:21 [worker.py:267] model weights take 2.44GiB; non_torch_memory takes 0.05GiB; PyTorch activation peak memory takes 1.05GiB; the rest of the memory reserved for KV Cache is 3.82GiB.
INFO 04-30 22:50:21 [executor_base.py:112] # cuda blocks: 6952, # CPU blocks: 3640
INFO 04-30 22:50:21 [executor_base.py:117] Maximum concurrency for 1024 tokens per request: 108.62x
INFO 04-30 22:50:21 [model_runner.py:1456] Capturing cudagraphs for decoding. This may lead to unexpected consequences if the model is not static. To run the model in eager mode, set 'enforce_eager=True' or use '--enforce-eager' in the CLI. If 

Capturing CUDA graph shapes:   0%|          | 0/27 [00:00<?, ?it/s]

INFO 04-30 22:50:38 [model_runner.py:1598] Graph capturing finished in 14 secs, took 0.57 GiB
INFO 04-30 22:50:38 [llm_engine.py:449] init engine (profile, create kv cache, warmup model) took 17.77 seconds


Unsloth 2025.4.1 patched 36 layers with 36 QKV layers, 36 O layers and 36 MLP layers.


### Data Prep
<a name="Data"></a>



In [3]:
import re
from datasets import load_dataset, Dataset

# Load and prep dataset
SYSTEM_PROMPT = """
Respond in the following format:
<reasoning>
...
</reasoning>
<answer>
...
</answer>
"""

def extract_xml_answer(text: str) -> str:
    answer = text.split("<answer>")[-1]
    answer = answer.split("</answer>")[0]
    return answer.strip()

def get_vi_gsm8k_questions(split="train") -> Dataset:
    data = load_dataset('hllj/vi_gsm8k')[split] 

    def normalize_answer(example):
        # Loại bỏ dấu phẩy trong số và chuyển thành dạng số nguyên
        example['answer'] = re.sub(r'[^\d]', '', example['answer'])
        return example

    data = data.map(normalize_answer) 

    data = data.map(lambda x: { 
        'prompt': [
            {'role': 'system', 'content': SYSTEM_PROMPT},
            {'role': 'user', 'content': x['question']}
        ],
    })  

    return data  

dataset = get_vi_gsm8k_questions(split = "train")
test_dataset = get_vi_gsm8k_questions(split = "test")

In [4]:
dataset

Dataset({
    features: ['index', 'explanation', 'question', 'answer', 'prompt'],
    num_rows: 7473
})

In [5]:
all_int = all(str(answer).isdigit() for answer in dataset['answer'])

print("Col 'answer' is full int?", all_int)

Col 'answer' is full int? True


### Reward function

In [6]:
def correctness_reward_func(prompts, completions, answer, **kwargs) -> list[float]:
    responses = [completion[0]['content'] for completion in completions]
    q = prompts[0][-1]['content']
    extracted_responses = [extract_xml_answer(r) for r in responses]
    print('-'*20, f"Question:\n{q}", f"\nAnswer:\n{answer[0]}", f"\nResponse:\n{responses[0]}", f"\nExtracted:\n{extracted_responses[0]}")
    return [2.0 if r == a else 0.0 for r, a in zip(extracted_responses, answer)]

def int_reward_func(completions, **kwargs) -> list[float]:
    responses = [completion[0]['content'] for completion in completions]
    extracted_responses = [extract_xml_answer(r) for r in responses]
    return [0.5 if r.isdigit() else 0.0 for r in extracted_responses]

def strict_format_reward_func(completions, **kwargs) -> list[float]:
    """Reward function that checks if the completion has a specific format."""
    pattern = r"^<reasoning>\n.*?\n</reasoning>\n<answer>\n.*?\n</answer>\n$"
    responses = [completion[0]["content"] for completion in completions]
    matches = [re.match(pattern, r) for r in responses]
    return [0.5 if match else 0.0 for match in matches]

def soft_format_reward_func(completions, **kwargs) -> list[float]:
    """Reward function that checks if the completion has a specific format."""
    pattern = r"<reasoning>.*?</reasoning>\s*<answer>.*?</answer>"
    responses = [completion[0]["content"] for completion in completions]
    matches = [re.match(pattern, r) for r in responses]
    return [0.5 if match else 0.0 for match in matches]

def count_xml(text) -> float:
    count = 0.0
    if text.count("<reasoning>\n") == 1:
        count += 0.125
    if text.count("\n</reasoning>\n") == 1:
        count += 0.125
    if text.count("\n<answer>\n") == 1:
        count += 0.125
        count -= len(text.split("\n</answer>\n")[-1])*0.001
    if text.count("\n</answer>") == 1:
        count += 0.125
        count -= (len(text.split("\n</answer>")[-1]) - 1)*0.001
    return count

def xmlcount_reward_func(completions, **kwargs) -> list[float]:
    contents = [completion[0]["content"] for completion in completions]
    return [count_xml(c) for c in contents]

In [7]:
max_len = max(dataset.map(
  lambda x: {"tokens": tokenizer.apply_chat_template(
  x["prompt"], add_generation_prompt=True, tokenize=True)},
  batched=True,
).map(lambda x: {"length": len(x["tokens"])})["length"])

In [8]:
max_len

427

In [9]:
max_prompt_length = max_len + 1

<a name="Train"></a>
### Train the model

Now set up GRPO Trainer and all configurations!

In [ ]:
from trl import GRPOConfig, GRPOTrainer
training_args = GRPOConfig(
    use_vllm = True, 
    learning_rate = 5e-6,
    weight_decay = 0.1,
    adam_beta1 = 0.9,
    adam_beta2 = 0.99,
    warmup_ratio = 0.1,
    lr_scheduler_type = "cosine",
    optim = "paged_adamw_8bit",
    logging_steps = 1,
    bf16 = is_bfloat16_supported(),
    fp16 = not is_bfloat16_supported(),
    per_device_train_batch_size = 1,
    gradient_accumulation_steps = 4,
    num_generations = 8,
    max_prompt_length = max_prompt_length,
    max_completion_length = max_seq_length - max_prompt_length,
    # num_train_epochs=1,
    max_steps = 1000,
    save_steps = 250,
    max_grad_norm = 0.1,
    report_to = "wandb",
    output_dir = "outputs_2",
)

Unsloth: We now expect `per_device_train_batch_size` to be a multiple of `num_generations`.
We will change the batch size of 1 to the `num_generations` of 8


In [11]:
trainer = GRPOTrainer(
    model = model,
    processing_class = tokenizer,
    reward_funcs = [
        xmlcount_reward_func,
        soft_format_reward_func,
        strict_format_reward_func,
        int_reward_func,
        correctness_reward_func,
    ],
    args = training_args,
    train_dataset = dataset,
    eval_dataset= test_dataset
)
trainer.train()

==((====))==  Unsloth - 2x faster free finetuning | Num GPUs used = 1
   \\   /|    Num examples = 7,473 | Num Epochs = 1 | Total steps = 1,000
O^O/ \_/ \    Batch size per device = 8 | Gradient accumulation steps = 4
\        /    Data Parallel GPUs = 1 | Total batch size (8 x 4 x 1) = 32
 "-____-"     Trainable parameters = 119,734,272/3,000,000,000 (3.99% trained)
wandb: WARNING The `run_name` is currently set to the same value as `TrainingArguments.output_dir`. If this was not intended, please specify a different run name by setting the `TrainingArguments.run_name` parameter.
wandb: Currently logged in as: tridungluong123 (tridungluong123-university) to https://api.wandb.ai. Use `wandb login --relogin` to force relogin


-------------------- Question:
Một vé concert có giá $40. Ông Benson đã mua 12 vé và nhận được giảm giá 5% cho mỗi vé được mua vượt quá 10. Tổng cộng ông Benson đã trả bao nhiêu tiền? 
Answer:
476 
Response:
<reasoning>
Trước hết, cần tính tổng số vé đã được giảm giá. Ông Benson đã mua 12 vé concert, cho nên 12 - 10 = 2 vé vượt quá 10 vé nên sẽ được giảm giá. Giả sử giá vé ban đầu là $40, giảm giá 5% cho mỗi vé vượt quá 10, thì mỗi vé giảm giá tương ứng là $40 * 5% = $2. Tổng số vé được giảm giá là 2, nên tổng giá giảm là 2 * $2 = $4. Tổng số vé bình thường mà ông Benson mua là 12 - 2 = 10 vé nên tổng giá trị của vé bình thường là 10 * $40 = $400. Ngoài ra, ông còn mua 2 vé vượt quá 10 vé và đã được giảm giá, giá trị của 2 vé đó là $4. Vậy tổng giá ông đã trả cho 12 vé trọn vẹn là 400 + 2 = $402.
</reasoning>
<answer>
$402
</answer> 
Extracted:
$402
-------------------- Question:
Jane đang cân nhắc giữa việc mua một căn nhà hoặc một chiếc rơ moóc. Một căn nhà có giá là $480,000 và một 

-------------------- Question:
Trong vòng 5 năm qua, vào ngày 4 tháng 7, nhiệt độ cao nhất tại Washington, DC là: 90 độ vào năm 2020, 90 độ vào năm 2019, 90 độ vào năm 2018, 79 độ vào năm 2017 và 71 độ vào năm 2016. Nhiệt độ trung bình cho ngày 4 tháng 7 tại Washington, DC trong vòng 5 năm qua là bao nhiêu? 
Answer:
84 
Response:
<reasoning>
Ở đây, chúng ta cần tính nhiệt độ trung bình cho ngày 4 tháng 7 trong vòng 5 năm. Đầu tiên chúng ta cần sưu tầm các dữ liệu nhiệt độ cao nhất vào ngày này trong các năm liên tiếp từ 2016 đến 2020. Dữ liệu đã được cung cấp như sau: 2016 - 71 độ, 2017 - 79 độ, 2018 - 90 độ, 2019 - 90 độ, 2020 - 90 độ. Nhiệt độ này chỉ phản ánh nhiệt độ cao nhất trong ngày mà không bao quát nhiệt độ trung bình trong cả ngày. Tuy nhiên, để làm cho câu hỏi trở nên đơn giản, chúng ta giả định rằng nhiệt độ cao nhất là mô tả cho cả ngày. 

Bây giờ, chúng ta sẽ tính trung bình cho năm năm đó:
1. Trích ra giá trị của năm năm: 71, 79, 90, 90, 90.
2. Tính tổng của giá trị: 71

TrainOutput(global_step=1000, training_loss=32325.679787395973, metrics={'train_runtime': 35026.8297, 'train_samples_per_second': 0.914, 'train_steps_per_second': 0.029, 'total_flos': 0.0, 'train_loss': 32325.679787395973})

<a name="Inference"></a>
### Inference
No LoRA

In [74]:
text = tokenizer.apply_chat_template([
    {"role" : "user", "content" : "Có tất cả bao nhiêu kí tự 'r' trong từ 'waterrmelon' ?"},
], tokenize = False, add_generation_prompt = True)

from vllm import SamplingParams
sampling_params = SamplingParams(
    temperature = 0.7,
    top_p = 0.95,
    max_tokens = 1024,
)
output = model.fast_generate(
    text,
    sampling_params=sampling_params,
    lora_request = None,
)[0].outputs[0].text

output

Processed prompts:   0%|          | 0/1 [00:00<?, ?it/s, est. speed input: 0.00 toks/s, output: 0.00 toks/s]

'Trong từ "watermelon", có 1 ký tự \'r\'.'

with the LoRA - GRPO

In [38]:
model.save_lora("grpo_saved_lora")

Now we load the LoRA and test:

In [60]:
text = tokenizer.apply_chat_template([
    {"role" : "system", "content" : SYSTEM_PROMPT},
    {"role" : "user", "content" : "Có tất cả bao nhiêu kí tự 'r' trong từ 'waterrmelon' ?"},
], tokenize = False, add_generation_prompt = True)

from vllm import SamplingParams
sampling_params = SamplingParams(
    temperature = 0.7,
    top_p = 0.95,
    max_tokens = 1024,
    skip_special_tokens=False,
)
output = model.fast_generate(
    text,
    sampling_params = sampling_params,
    lora_request = model.load_lora("grpo_saved_lora"),
)

output[0].outputs[0].text

Processed prompts:   0%|          | 0/1 [00:00<?, ?it/s, est. speed input: 0.00 toks/s, output: 0.00 toks/s]

'<reasoning>\nKhi phân tích từ "waterrmelon", ta thấy nó có một lỗi chính tả (do có hai chữ \'r\'). Mặc dù vậy, ta cần phân tích từ nguyên vẹn là "watermelon". Từ "watermelon" chỉ có một ký tự \'r\'. Ký tự \'r\' xuất hiện hai lần trong từ này (ở vị trí thứ 1 và thứ 8). Tuy nhiên, theo yêu cầu, ta cần đếm tất cả các ký tự \'r\' nên kết quả sẽ là hai ký tự.\n</reasoning>\n<answer>\n2\n</answer>\n'

In [28]:
torch.cuda.empty_cache()

<a name="Save"></a>
### Saving to float16 for VLLM


In [ ]:
import os
# os.environ["HF_TOKEN"] = "hidden"

In [133]:
# Merge to 16bit
if False: model.save_pretrained_merged("model", tokenizer, save_method = "merged_16bit",)
if True: model.push_to_hub_merged("binhphap5/Qwen2.5-3b-vi_gsm8k-grpo", tokenizer, save_method = "merged_16bit", token = os.environ["HF_TOKEN"])

Unsloth: You are pushing to hub, but you passed your HF username = binhphap5.
We shall truncate binhphap5/Qwen2.5-3b-vi_gsm8k-grpo to Qwen2.5-3b-vi_gsm8k-grpo


Unsloth: Merging 4bit and LoRA weights to 16bit...
Unsloth: Will use up to 0.0 out of 15.53 RAM for saving.
Unsloth: Saving model... This might take 5 minutes ...


 81%|████████  | 29/36 [00:00<00:00, 57.28it/s]
We will save to Disk and not RAM now.
100%|██████████| 36/36 [00:01<00:00, 24.39it/s]


Unsloth: Saving tokenizer...

No files have been modified since last commit. Skipping to prevent empty commit.


...

README.md:   0%|          | 0.00/617 [00:00<?, ?B/s]

  0%|          | 0/2 [00:00<?, ?it/s]

model-00001-of-00002.safetensors:   0%|          | 0.00/4.96G [00:00<?, ?B/s]

model-00002-of-00002.safetensors:   0%|          | 0.00/1.21G [00:00<?, ?B/s]

Done.
Saved merged model to https://huggingface.co/binhphap5/Qwen2.5-3b-vi_gsm8k-grpo


# benchmark

In [29]:
test_dataset

Dataset({
    features: ['index', 'explanation', 'question', 'answer', 'prompt'],
    num_rows: 1319
})

In [122]:
import tqdm
tokenizer.padding_side = "left"

def extract_reason_answer(text: str) -> dict:
    reasoning = text.split("<reasoning>")[-1]
    reasoning = reasoning.split("</reasoning>")[0]
    answer = text.split("<answer>")[-1]
    answer = answer.split("</answer>")[0]
    return {
        "reasoning": reasoning.strip(),
        "answer": answer.strip(),
        "raw": text
    }

def generate_batch_responses(input_texts, model, tokenizer, batch_size=10, max_length=768):
    all_responses = []

    for i in tqdm(range(0, len(input_texts), batch_size), desc="Generating responses"):
        batch_inputs = input_texts[i:i + batch_size]
        
        # Apply chat template for each input in the batch
        batch_prompts = []
        for text in batch_inputs:
            messages = [
                {"role": "system", "content": SYSTEM_PROMPT},
                {"role": "user", "content": text},
            ]
            prompt = tokenizer.apply_chat_template(
                messages,
                tokenize=False,
                add_generation_prompt=True  # Comment this for training
            )
            batch_prompts.append(prompt)
        
        # Generate for all inputs in batch
        with torch.no_grad():
            FastLanguageModel.for_inference(model)
            sampling_params = SamplingParams(
                temperature = 0.7,
                top_p = 0.95,
                max_tokens = max_length,
            )
            decoded_outputs = model.fast_generate(
                batch_prompts,
                sampling_params = sampling_params,
                lora_request = model.load_lora("grpo_saved_lora"),
            )

        responses = [
            extract_reason_answer(output.outputs[0].text)
            for output in decoded_outputs
        ]

        all_responses.extend(responses)

    return all_responses

In [123]:
tokenizer.padding_side

'left'

# Calculate Rouge

In [124]:
# Import required libraries
import torch
from tqdm import tqdm

# Get the first 100 samples from test dataset
test_sample = test_dataset.select(range(100))

# Extract validation inputs and references
val_inputs = [example["question"] for example in test_sample]

references = [example["answer"] for example in test_sample]
ref_reasonings = [example["explanation"] for example in test_sample]

# Generate predictions with batch processing
print("Generating predictions...")
predictions = generate_batch_responses(val_inputs, model, tokenizer)

# Example
print("\nFirst 3 examples:")
for i in range(3):
    print(f"\nInput: {val_inputs[i]}")
    print(f"Prediction Reasoning: {predictions[i]['reasoning']}")
    print(f"Prediction Answer: {predictions[i]['answer']}")
    print(f"Reference: {references[i]}")
    print("-" * 80)

Generating predictions...


Generating responses:   0%|          | 0/10 [00:00<?, ?it/s]

Processed prompts:   0%|          | 0/10 [00:00<?, ?it/s, est. speed input: 0.00 toks/s, output: 0.00 toks/s]

Generating responses:  10%|█         | 1/10 [00:07<01:04,  7.20s/it]

Processed prompts:   0%|          | 0/10 [00:00<?, ?it/s, est. speed input: 0.00 toks/s, output: 0.00 toks/s]

...

Processed prompts:   0%|          | 0/10 [00:00<?, ?it/s, est. speed input: 0.00 toks/s, output: 0.00 toks/s]

Generating responses:  90%|█████████ | 9/10 [01:09<00:06,  6.84s/it]

Processed prompts:   0%|          | 0/10 [00:00<?, ?it/s, est. speed input: 0.00 toks/s, output: 0.00 toks/s]

Generating responses: 100%|██████████| 10/10 [01:16<00:00,  7.62s/it]


First 3 examples:

Input: Vịt của Janet đẻ được 16 quả trứng mỗi ngày. Cô ấy ăn 3 quả vào bữa sáng và nướng bánh muffin cho bạn bè mỗi ngày với 4 quả. Cô ấy bán số trứng còn lại tại chợ nông sản hàng ngày với giá $2 mỗi quả trứng vịt tươi. Cô ấy kiếm được bao nhiêu đô la mỗi ngày tại chợ nông sản?
Prediction Reasoning: Janet đẻ trứng vịt mỗi ngày là 16 quả. Cô ấy ăn 3 quả trứng vào bữa sáng và làm bánh muffin với 4 quả trứng mỗi ngày. Số trứng còn lại sau khi ăn và làm bánh là 16 - 3 - 4 = 9 quả trứng. Cô ấy bán số trứng còn lại với giá 2 đô la cho mỗi quả trứng. Do đó, số tiền cô ấy kiếm được mỗi ngày là 9 quả trứng * 2 đô la/ quả trứng = 18 đô la.
Prediction Answer: 18
Reference: 18
--------------------------------------------------------------------------------

Input: Một chiếc áo choàng cần 2 cuộn sợi màu xanh và một nửa số đó là sợi màu trắng. Tổng cộng cần bao nhiêu cuộn sợi?
Prediction Reasoning: Chiếc áo choàng cần 2 cuộn sợi màu xanh. Một nửa số cuộn sợi màu xanh là 2/2 = 1 

In [125]:
predictions

[{'reasoning': 'Janet đẻ trứng vịt mỗi ngày là 16 quả. Cô ấy ăn 3 quả trứng vào bữa sáng và làm bánh muffin với 4 quả trứng mỗi ngày. Số trứng còn lại sau khi ăn và làm bánh là 16 - 3 - 4 = 9 quả trứng. Cô ấy bán số trứng còn lại với giá 2 đô la cho mỗi quả trứng. Do đó, số tiền cô ấy kiếm được mỗi ngày là 9 quả trứng * 2 đô la/ quả trứng = 18 đô la.',
  'answer': '18',
  'raw': '<reasoning>\nJanet đẻ trứng vịt mỗi ngày là 16 quả. Cô ấy ăn 3 quả trứng vào bữa sáng và làm bánh muffin với 4 quả trứng mỗi ngày. Số trứng còn lại sau khi ăn và làm bánh là 16 - 3 - 4 = 9 quả trứng. Cô ấy bán số trứng còn lại với giá 2 đô la cho mỗi quả trứng. Do đó, số tiền cô ấy kiếm được mỗi ngày là 9 quả trứng * 2 đô la/ quả trứng = 18 đô la.\n</reasoning>\n<answer>\n18\n</answer>\n'},
 {'reasoning': 'Chiếc áo choàng cần 2 cuộn sợi màu xanh. Một nửa số cuộn sợi màu xanh là 2/2 = 1 cuộn sợi màu trắng. Tổng cộng, cần 2 (màu xanh) + 1 (màu trắng) = 3 cuộn sợi.',
  'answer': '3',
  'raw': '<reasoning>\nChiếc 

In [126]:
# Calculate ROUGE scores
print("\nCalculating ROUGE scores on reasoning...")
from rouge_score import rouge_scorer

scorer = rouge_scorer.RougeScorer(['rouge1', 'rouge2', 'rougeL'], use_stemmer=True)

# Initialize
rouge_scores = {
    'rouge1': {'precision': 0.0, 'recall': 0.0, 'fmeasure': 0.0},
    'rouge2': {'precision': 0.0, 'recall': 0.0, 'fmeasure': 0.0},
    'rougeL': {'precision': 0.0, 'recall': 0.0, 'fmeasure': 0.0}
}

# Loop
for pred, ref in tqdm(zip(predictions, ref_reasonings), total=len(predictions), desc="Computing ROUGE"):
    pred_reasoning = pred["reasoning"]
    scores = scorer.score(ref, pred_reasoning)
    
    for metric in rouge_scores.keys():
        rouge_scores[metric]['precision'] += scores[metric].precision
        rouge_scores[metric]['recall'] += scores[metric].recall
        rouge_scores[metric]['fmeasure'] += scores[metric].fmeasure

# Average
n = len(predictions)
for metric in rouge_scores.keys():
    for key in rouge_scores[metric].keys():
        rouge_scores[metric][key] /= n

# Print
print("\nROUGE Scores:")
for metric, scores in rouge_scores.items():
    print(f"\n{metric}:")
    for key, value in scores.items():
        print(f"  {key}: {value:.4f}")


Calculating ROUGE scores on reasoning...


Computing ROUGE: 100%|██████████| 100/100 [00:00<00:00, 643.81it/s]


ROUGE Scores:

rouge1:
  precision: 0.4573
  recall: 0.7798
  fmeasure: 0.5475

rouge2:
  precision: 0.2482
  recall: 0.4231
  fmeasure: 0.2972

rougeL:
  precision: 0.3160
  recall: 0.5475
  fmeasure: 0.3795


# Calculate sacrebleu score

In [127]:
# Calculate sacrebleu score
import sacrebleu

# Prepare references and predictions for sacrebleu
pred_texts = [pred['reasoning'] for pred in predictions] 
refs_for_sacrebleu = [[ref] for ref in ref_reasonings]

# Calculate sacrebleu
print("\nCalculating BLEU score on reasoning...")
bleu = sacrebleu.corpus_bleu(pred_texts, refs_for_sacrebleu)
print(f"\nSacreBLEU Score: {bleu.score:.4f}")


Calculating BLEU score on reasoning...

SacreBLEU Score: 31.5785


# Calculate Exact Match Score:

In [129]:
# Calculate Exact Match Score
exact_match_count = 0

for pred, ref_ans in zip(predictions, references):
    if pred['answer'].strip() == ref_ans.strip():
        exact_match_count += 1

exact_match_score = exact_match_count / len(predictions)

print(f"\nExact Match Score: {exact_match_score:.4f}")


Exact Match Score: 0.6700


In [130]:
exact_match_count

67

# Save metrics

In [131]:
# Save all metrics
import json
from datetime import datetime

# Create a summary dictionary of all metrics
evaluation_metrics = {
    'sacrebleu': bleu.score,
    'rouge_scores': rouge_scores,
    'exact_match_score': exact_match_score,
}

# Prepare metrics with timestamp for saving
metrics_filename = "./logs/qwen-2.5-3b-grpo-math-qa.json"
timestamp = datetime.now().strftime("%Y%m%d_%H%M%S")

metrics_to_save = {
    'timestamp': timestamp,
    'model_name': "./logs/qwen-2.5-3b-grpo-math-qa",
    'metrics': evaluation_metrics
}

# Print summary before saving
print(f"SacreBLEU Score: {evaluation_metrics['sacrebleu']:.4f}")
print("\nROUGE Scores Summary:")
for metric, scores in evaluation_metrics['rouge_scores'].items():
    print(f"{metric} F1: {scores['fmeasure']:.4f}")
print(f"\nExact Match Score: {evaluation_metrics['exact_match_score']:.4f}")

# Save to file
with open(metrics_filename, 'w', encoding='utf-8') as f:
    json.dump(metrics_to_save, f, indent=2, ensure_ascii=False)

print(f"\nMetrics saved to {metrics_filename}")

SacreBLEU Score: 31.5785

ROUGE Scores Summary:
rouge1 F1: 0.5475
rouge2 F1: 0.2972
rougeL F1: 0.3795

Exact Match Score: 0.6700

Metrics saved to ./logs/qwen-2.5-3b-grpo-math-qa.json
